In [1]:
# note: must run in virtual environment
import os
import sys
venv_path = os.environ['VIRTUAL_ENV']
sys.path.append(os.path.join(os.environ['VIRTUAL_ENV'], "lib\site-packages"))

In [2]:
import numpy as np
import matplotlib.pyplot as plt
import folium
import pandas as pd
from OSMPythonTools.nominatim import Nominatim
from scipy import stats
%matplotlib inline

In [3]:
CITY = "accident_yishuv_name"
LAT_DB = "latitude"
LONG_DB = "longitude"
LAT_NOMINATIM = "lat"
LONG_NOMINATIM = "lon"

DEFAULT_ZOOM = 15

In [4]:
csv_path = "involved_markers_hebrew.csv"
data = pd.read_csv(csv_path)

c:\users\asya\appdata\local\programs\python\python37\lib\site-packages\IPython\core\interactiveshell.py:3051: DtypeWarning: Columns (36,38,40,44,91,93,130,144,153) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [5]:
nominatim = Nominatim()

def get_city_coord(city_name):
    # find coord of city using Nominatim server. 
    # Assumption: the city is the first result returned
    result = nominatim.query(city_name).toJSON()[0]
    city_coord = [result['lat'], result['lon']]
    return city_coord

def add_html_text(text, coord):
    iframe = folium.IFrame(html=text, width=250, height=200)
    popup = folium.Popup(iframe, max_width=3000)

    text_marker = folium.Marker(location=coord, popup=popup,
                     icon=folium.Icon(icon_color='green'))
    return text_marker

def create_city_desc(city_data, city_name):
    title_heb = "פיזור תאונות ב" + city_name
    num_accidents = len(city_data)
    num_coords = len(city_data[[LAT_DB, LONG_DB]].drop_duplicates())
    txt_heb = str(num_accidents) + " תאונות ב-" + str(num_coords) + " מוקדים"
    html = "<h2 dir='rtl'>" + title_heb + "</h2><p dir='rtl'>" + txt_heb + "</p>"
    return html
    
def plot_city(data, city_name):
    city_coord = get_city_coord(city_name)
    
    city_data = data.loc[data[CITY] == city_name].drop_duplicates()
    coords = city_data[[LAT_DB, LONG_DB]].values
    
    # create map and add all accidents to map
    map = folium.Map(location=city_coord, zoom_start=DEFAULT_ZOOM)
    for coord in coords:
        folium.Marker(coord).add_to(map)
    
    # add text marker to describe city data
    text = create_city_desc(city_data, city_name)
    text_marker = add_html_text(text, city_coord)
    map.add_child(text_marker)
    return map

In [6]:
plot_city(data, "טייבה")

In [7]:
plot_city(data, "טבריה")